# Finding The Optimal Neighborhood For Any Venue Type In New York City

## Introduction / Busniess Problem

For the capstone project, I aim to utilize the Foursquare API to provide insights regarding location selection for any type of venue. With the Foursqaure API, we can see the existing venues in New York City and in which neighborhoods they are concentrated. From this location data, we can recommeded the best neighborhood for a particular type of business so that business would florish.

In [2]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

# !conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

# !conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


## Data Extraction

We will utilize the new york data given in the labs to construct our data set. We will utilize the entirety of neighborhoods in or around new york city for this project.

In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [5]:
neighborhoods_data = newyork_data['features']

In [6]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
ny_neighborhoods = pd.DataFrame(columns=column_names)

In [7]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    ny_neighborhoods = ny_neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [8]:
ny_neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [9]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude

In [10]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(ny_neighborhoods['Latitude'], ny_neighborhoods['Longitude'], ny_neighborhoods['Borough'], ny_neighborhoods['Neighborhood']):
    label = '{}, {}'.format(ny_neighborhoods, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [11]:
ny_neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [16]:
CLIENT_ID = 'V1YPB05DJJGQD12QBQNUQUAIKUJZL3NUZIHOIG4GTPLCTY0I' # your Foursquare ID
CLIENT_SECRET = 'OQX0ME53ARGSBG45YSRCZTHBX04FYGDIKIJ2L04XZ2LOYJ3L' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

In [17]:
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [18]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [19]:
ny_venues = getNearbyVenues(names=ny_neighborhoods['Neighborhood'],
                                   latitudes=ny_neighborhoods['Latitude'],
                                   longitudes=ny_neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

In [20]:
print(ny_venues.shape)
ny_venues.head()

(10263, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3         Walgreens       40.896687       -73.844850        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

Notice that some neighborhoods have less venues and some have greater number of venues.

In [21]:
ny_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      30                      30   
Annadale                                      11                      11   
Arden Heights                                  5                       5   
Arlington                                      5                       5   
Arrochar                                      20                      20   
Arverne                                       18                      18   
Astoria                                      100                     100   
Astoria Heights                               14                      14   
Auburndale                                    19                      19   
Bath Beach                                    50                      50   
Battery Park City                             95                      95   
Bay Ridge                                     85                      85   
Bay Terrace                                   48                      48   
Baychester                                    21                      21   
Bayside                                       78                      78   
Bayswater                                      3                       3   
Bedford Park                                  36                      36   
Bedford Stuyvesant                            27                      27   
Beechhurst                                    15                      15   
Bellaire                                      15                      15   
Belle Harbor                                  17                      17   
Bellerose                                     19                      19   
Belmont                                       96                      96   
Bensonhurst                                   35                      35   
Bergen Beach                                   7                       7   
Blissville                                    19                      19   
Bloomfield                                     5                       5   
Boerum Hill                                   88                      88   
Borough Park                                  19                      19   
Breezy Point                                   4                       4   
Briarwood                                     11                      11   
Brighton Beach                                45                      45   
Broad Channel                                  5                       5   
Broadway Junction                             17                      17   
Bronxdale                                     12                      12   
Brooklyn Heights                             100                     100   
Brookville                                     1                       1   
Brownsville                                   20                      20   
Bulls Head                                    44                      44   
Bushwick                                      75                      75   
Butler Manor                                   5                       5   
Cambria Heights                               15                      15   
Canarsie                                       7                       7   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Castle Hill                                    8                       8   
Castleton Corners                             15                      15   
Central Harlem                                43                      43   
Charleston                                    29                      29   
Chelsea                                      106                     106   
Chinatown                                    100                     100   

In [22]:
print('There are {} uniques venues.'.format(len(ny_venues['Venue Category'].unique())))

There are 431 uniques venues.


In [32]:
ny_neighborhoods = ny_neighborhoods.drop('Borough', axis = 1)
ny_neighborhoods.head()

Neighborhood   Latitude  Longitude
0    Wakefield  40.894705 -73.847201
1   Co-op City  40.874294 -73.829939
2  Eastchester  40.887556 -73.827806
3    Fieldston  40.895437 -73.905643
4    Riverdale  40.890834 -73.912585

In [24]:
ny_venues.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3         Walgreens       40.896687       -73.844850        Pharmacy  
4           Dunkin'       40.890459       -73.849089      Donut Shop

## Data Preperation 

Since the problem is to provide a location for a particular venue, we will have the features being the venues type and the target varaible being the longitude and latitude location.

In [28]:
features = ny_venues[{'Venue Category'}]
target = ny_venues[{'Venue Longitude',  'Venue Longitude'}]

In [30]:
features = pd.get_dummies(features[{'Venue Category'}])

In [31]:
features.head()
features.shape

(10263, 431)